In [65]:
import numpy as np
import pandas as pd
import plotly.express as px
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [66]:
#loading the dataset
df=pd.read_csv('/kaggle/input/chess/games.csv')
#showing the dataset
df

id  rated    created_at  last_move_at  turns victory_status  \
0      TZJHLljE  False  1.504210e+12  1.504210e+12     13      outoftime   
1      l1NXvwaE   True  1.504130e+12  1.504130e+12     16         resign   
2      mIICvQHh   True  1.504130e+12  1.504130e+12     61           mate   
3      kWKvrqYL   True  1.504110e+12  1.504110e+12     61           mate   
4      9tXo1AUZ   True  1.504030e+12  1.504030e+12     95           mate   
...         ...    ...           ...           ...    ...            ...   
20053  EfqH7VVH   True  1.499791e+12  1.499791e+12     24         resign   
20054  WSJDhbPl   True  1.499698e+12  1.499699e+12     82           mate   
20055  yrAas0Kj   True  1.499698e+12  1.499698e+12     35           mate   
20056  b0v4tRyF   True  1.499696e+12  1.499697e+12    109         resign   
20057  N8G2JHGG   True  1.499643e+12  1.499644e+12     78           mate   

      winner increment_code       white_id  white_rating            black_id  \
0      white           15+2       bourgris          1500                a-00   
1      black           5+10           a-00          1322           skinnerua   
2      white           5+10         ischia          1496                a-00   
3      white           20+0  daniamurashov          1439        adivanov2009   
4      white           30+3      nik221107          1523        adivanov2009   
...      ...            ...            ...           ...                 ...   
20053  white          10+10        belcolt          1691            jamboger   
20054  black           10+0       jamboger          1233  farrukhasomiddinov   
20055  white           10+0       jamboger          1219        schaaksmurf3   
20056  white           10+0   marcodisogno          1360            jamboger   
20057  black           10+0       jamboger          1235               ffbob   

       black_rating                                              moves  \
0              1191  d4 d5 c4 c6 cxd5 e6 dxe6 fxe6 Nf3 Bb4+ Nc3 Ba5...   
1              1261  d4 Nc6 e4 e5 f4 f6 dxe5 fxe5 fxe5 Nxe5 Qd4 Nc6...   
2              1500  e4 e5 d3 d6 Be3 c6 Be2 b5 Nd2 a5 a4 c5 axb5 Nc...   
3              1454  d4 d5 Nf3 Bf5 Nc3 Nf6 Bf4 Ng4 e3 Nc6 Be2 Qd7 O...   
4              1469  e4 e5 Nf3 d6 d4 Nc6 d5 Nb4 a3 Na6 Nc3 Be7 b4 N...   
...             ...                                                ...   
20053          1220  d4 f5 e3 e6 Nf3 Nf6 Nc3 b6 Be2 Bb7 O-O Be7 Ne5...   
20054          1196  d4 d6 Bf4 e5 Bg3 Nf6 e3 exd4 exd4 d5 c3 Bd6 Bd...   
20055          1286  d4 d5 Bf4 Nc6 e3 Nf6 c3 e6 Nf3 Be7 Bd3 O-O Nbd...   
20056          1227  e4 d6 d4 Nf6 e5 dxe5 dxe5 Qxd1+ Kxd1 Nd5 c4 Nb...   
20057          1339  d4 d5 Bf4 Na6 e3 e6 c3 Nf6 Nf3 Bd7 Nbd2 b5 Bd3...   

      opening_eco                            opening_name  opening_ply  
0             D10        Slav Defense: Exchange Variation            5  
1             B00  Nimzowitsch Defense: Kennedy Variation            4  
2             C20   King's Pawn Game: Leonardis Variation            3  
3             D02  Queen's Pawn Game: Zukertort Variation            3  
4             C41                        Philidor Defense            5  
...           ...                                     ...          ...  
20053         A80                           Dutch Defense            2  
20054         A41                            Queen's Pawn            2  
20055         D00         Queen's Pawn Game: Mason Attack            3  
20056         B07                            Pirc Defense            4  
20057         D00         Queen's Pawn Game: Mason Attack            3  

[20058 rows x 16 columns]

In [67]:
moves=np.array(df.query("winner!='draw'")['moves'])

In [68]:
moves

array(['d4 d5 c4 c6 cxd5 e6 dxe6 fxe6 Nf3 Bb4+ Nc3 Ba5 Bf4',
       'd4 Nc6 e4 e5 f4 f6 dxe5 fxe5 fxe5 Nxe5 Qd4 Nc6 Qe5+ Nxe5 c4 Bb4+',
       'e4 e5 d3 d6 Be3 c6 Be2 b5 Nd2 a5 a4 c5 axb5 Nc6 bxc6 Ra6 Nc4 a4 c3 a3 Nxa3 Rxa3 Rxa3 c4 dxc4 d5 cxd5 Qxd5 exd5 Be6 Ra8+ Ke7 Bc5+ Kf6 Bxf8 Kg6 Bxg7 Kxg7 dxe6 Kh6 exf7 Nf6 Rxh8 Nh5 Bxh5 Kg5 Rxh7 Kf5 Qf3+ Ke6 Bg4+ Kd6 Rh6+ Kc5 Qe3+ Kb5 c4+ Kb4 Qc3+ Ka4 Bd1#',
       ...,
       'd4 d5 Bf4 Nc6 e3 Nf6 c3 e6 Nf3 Be7 Bd3 O-O Nbd2 b6 Ne5 Nxe5 Bxe5 Nd7 Bxh7+ Kxh7 Qh5+ Kg8 Nf3 f6 Bf4 g5 Qg6+ Kh8 Nh4 Qe8 Qh6+ Kg8 Ng6 Kf7 Qh7#',
       'e4 d6 d4 Nf6 e5 dxe5 dxe5 Qxd1+ Kxd1 Nd5 c4 Nb6 c5 Nd5 Bc4 e6 Bxd5 exd5 Nc3 d4 Ne4 Bf5 f3 Nd7 b4 Nxe5 Bf4 f6 g4 Bxe4 fxe4 c6 Bxe5 fxe5 Nf3 Be7 Nxe5 Bf6 Nc4 O-O-O h4 h6 e5 b5 cxb6 Be7 bxa7 Kc7 a3 Rhf8 Kd2 Rf4 Rag1 d3 h5 Rf2+ Ke3 Re2+ Kf4 Rf8+ Kg3 Re3+ Nxe3 d2 Rd1 Bg5 Nf5 Kb7 Rhf1 Kxa7 Nd6 Rxf1 Rxf1 Kb6 e6 Kc7 Nf5 Kc8 e7 Kd7 a4 Bxe7 Nxe7 Kxe7 a5 Kd7 Rd1 Kc7 Rxd2 Kb7 Ra2 Ka6 Kf4 Kb5 a6 Kb6 a7 Kb5 a8=Q Kxb4 Qxc6 g5+ hxg6 Kb3 Rc

In [69]:
winner=np.array(df.query("winner!='draw'")['winner'])

In [70]:
winner = np.array([1 if x == 'white' else 0 for x in winner])

In [71]:
winner

array([1, 0, 1, ..., 1, 1, 0])

In [72]:
moves.shape

(19108,)

In [73]:
winner.shape

(19108,)

In [74]:
all_moves=set()

for move in moves:
    for move in move.split(' '):
        if move not in all_moves:
            all_moves.add(move)
move_length=len(all_moves)

In [75]:
print(move_length)

4373


In [76]:
max_len=0

for move in moves:
    total=0
    for move in move.split(' '):
        total+=1
    if total>max_len:
        max_len=total
print(max_len)


349


In [77]:
tokenizer=Tokenizer(num_words=move_length)
tokenizer.fit_on_texts(moves)
sequences=tokenizer.texts_to_sequences(moves)
print(sequences)

[[5, 8, 11, 22, 73, 12, 481, 250, 2, 60, 9, 363, 58], [5, 7, 3, 6, 19, 49, 64, 158, 158, 41, 161, 7, 169, 41, 11, 60], [3, 6, 29, 13, 36, 22, 54, 15, 84, 34, 32, 10, 222, 7, 45, 329, 122, 32, 21, 26, 675, 503, 503, 11, 152, 8, 73, 112, 27, 65, 196, 76, 56, 115, 513, 124, 402, 479, 481, 265, 780, 4, 682, 190, 640, 188, 498, 160, 72, 120, 47, 142, 432, 248, 145, 361, 11, 338, 202, 521, 563], [5, 8, 2, 75, 9, 4, 58, 110, 44, 7, 54, 95, 1, 1, 1, 1, 1, 136, 149, 96, 702, 198, 149, 654, 299, 136, 540, 518, 331, 81, 201, 716, 101, 165, 45, 549, 511, 475, 6, 453, 76, 64, 205, 266, 120, 280, 160, 332, 4, 213, 188, 43, 110, 172, 337, 327, 265, 172, 35, 89, 246, 492, 70, 400], [3, 6, 2, 13, 5, 7, 8, 149, 26, 285, 9, 24, 23, 4, 30, 1, 1, 15, 118, 78, 78, 31, 95, 1, 1, 380, 271, 22, 32, 73, 66, 153, 304, 134, 573, 61, 304, 85, 51, 186, 199, 171, 364, 46, 259, 47, 171, 244, 252, 92, 433, 77, 391, 82, 267, 146, 324, 97, 21, 163, 57, 218, 444, 49, 446, 82, 74, 124, 401, 454, 151, 96, 88, 218, 133, 42,

In [78]:
word_index=tokenizer.word_index
print(word_index)

{'o': 1, 'nf3': 2, 'e4': 3, 'nf6': 4, 'd4': 5, 'e5': 6, 'nc6': 7, 'd5': 8, 'nc3': 9, 'c5': 10, 'c4': 11, 'e6': 12, 'd6': 13, 'a6': 14, 'b5': 15, 'h3': 16, 'h6': 17, 'bc4': 18, 'f4': 19, 'g6': 20, 'c3': 21, 'c6': 22, 'b4': 23, 'be7': 24, 'f5': 25, 'a3': 26, 'exd5': 27, 're1': 28, 'd3': 29, 'bg5': 30, 'bd3': 31, 'a4': 32, 'g4': 33, 'a5': 34, 'g5': 35, 'be3': 36, 'ne5': 37, 'nxd4': 38, 'bb5': 39, 'h4': 40, 'nxe5': 41, 'h5': 42, 'g3': 43, 'e3': 44, 'bxc6': 45, 're8': 46, 'bg4': 47, 'ne4': 48, 'f6': 49, 'b6': 50, 'nd5': 51, 'bxc3': 52, 'cxd4': 53, 'be2': 54, 'bd6': 55, 'bc5': 56, 'f3': 57, 'bf4': 58, 'b3': 59, 'bb4': 60, 'bd7': 61, 'nd4': 62, 'nxe4': 63, 'dxe5': 64, 'be6': 65, 'nxd5': 66, 'qe2': 67, 'qe7': 68, 'exd4': 69, 'bg7': 70, 'bd2': 71, 'qf3': 72, 'cxd5': 73, 'rd1': 74, 'bf5': 75, 'ke7': 76, 'rd8': 77, 'bxf6': 78, 'nd7': 79, 'bb7': 80, 'qd2': 81, 'kg7': 82, 'ng5': 83, 'nd2': 84, 'rc8': 85, 'kf7': 86, 'ke2': 87, 'kf2': 88, 'qf6': 89, 'ne7': 90, 'kg2': 91, 'bxf3': 92, 'qc7': 93, 'q': 9

In [79]:
model_inputs=pad_sequences(sequences,maxlen=max_len)

model_inputs

array([[  0,   0,   0, ...,   9, 363,  58],
       [  0,   0,   0, ...,  41,  11,  60],
       [  0,   0,   0, ..., 202, 521, 563],
       ...,
       [  0,   0,   0, ..., 194,  86, 528],
       [  0,   0,   0, ..., 360, 505,  85],
       [  0,   0,   0, ..., 247, 177, 280]], dtype=int32)

In [80]:
model_inputs.shape

(19108, 349)

In [81]:
winner.shape

(19108,)

# Training

In [82]:
train_inputs,test_inputs,train_labels,test_labels=train_test_split(model_inputs,winner,train_size=0.7,random_state=123)

In [83]:
print(train_inputs.shape)
print(test_inputs.shape)
print(train_labels.shape)
print(test_labels.shape)

(13375, 349)
(5733, 349)
(13375,)
(5733,)


In [84]:
print(max_len)

349


In [85]:
import tensorflow as tf

embedding_dim = 256
max_len = max_len  
max_vocab = max_vocab  

inputs = tf.keras.Input(shape=(max_len,))

embedding = tf.keras.layers.Embedding(input_dim=max_vocab,
                                      output_dim=embedding_dim,
                                      input_length=max_len)(inputs)

gru = tf.keras.layers.GRU(units=embedding_dim)(embedding)
outputs = tf.keras.layers.Dense(1, activation='sigmoid')(gru)

model = tf.keras.Model(inputs=inputs, outputs=outputs)

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy', tf.keras.metrics.AUC(name='auc')])

batch_size = 32
epochs = 10

# Assuming train_inputs and train_labels are already defined
history = model.fit(train_inputs, train_labels, validation_split=0.2, batch_size=batch_size, epochs=epochs,
                    callbacks=[tf.keras.callbacks.ReduceLROnPlateau()])

print("Model training complete.")


Epoch 1/10


/opt/conda/lib/python3.10/site-packages/keras/src/layers/core/embedding.py:90: UserWarning:

Argument `input_length` is deprecated. Just remove it.



335/335 ━━━━━━━━━━━━━━━━━━━━ 10s 24ms/step - accuracy: 0.6746 - auc: 0.7425 - loss: 0.5955 - val_accuracy: 0.7492 - val_auc: 0.8228 - val_loss: 0.5176 - learning_rate: 0.0010
Epoch 2/10
335/335 ━━━━━━━━━━━━━━━━━━━━ 8s 24ms/step - accuracy: 0.8095 - auc: 0.8897 - loss: 0.4216 - val_accuracy: 0.8658 - val_auc: 0.9387 - val_loss: 0.3270 - learning_rate: 0.0010
Epoch 3/10
335/335 ━━━━━━━━━━━━━━━━━━━━ 8s 24ms/step - accuracy: 0.8809 - auc: 0.9523 - loss: 0.2801 - val_accuracy: 0.8744 - val_auc: 0.9490 - val_loss: 0.2911 - learning_rate: 0.0010
Epoch 4/10
335/335 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step - accuracy: 0.9040 - auc: 0.9684 - loss: 0.2284 - val_accuracy: 0.8778 - val_auc: 0.9496 - val_loss: 0.2876 - learning_rate: 0.0010
Epoch 5/10
335/335 ━━━━━━━━━━━━━━━━━━━━ 8s 24ms/step - accuracy: 0.9288 - auc: 0.9807 - loss: 0.1794 - val_accuracy: 0.8419 - val_auc: 0.9198 - val_loss: 0.3661 - learning_rate: 0.0010
Epoch 6/10
335/335 ━━━━━━━━━━━━━━━━━━━━ 8s 22ms/step - accuracy: 0.9142 - auc: 0.9734

In [86]:
fig=px.line(history.history,y=['auc','val_auc'],labels={'x':'Epochs','y':'AUC'},
           title='AUC Over Time')

fig.show()


In [87]:
fig=px.line(history.history,y=['loss','val_auc'],labels={'x':'Epochs','y':'Loss'},
           title='Loss Over Time')

fig.show()


In [88]:
model.evaluate(test_inputs,test_labels)

180/180 ━━━━━━━━━━━━━━━━━━━━ 2s 9ms/step - accuracy: 0.8618 - auc: 0.9293 - loss: 0.4783


[0.45366522669792175, 0.8644688725471497, 0.9332339763641357]